# Introduction

This is our group data-visualisation project.
The goal is to get insight in a fun dataset: names of babies in France between 1900 and 2020.

Let's get started !

In [13]:
import polars as pl
import json
import altair as alt

In [14]:
babies = pl.read_csv("data/dataset.csv", schema_overrides={"dpt": pl.String})

In [15]:
is_rare = pl.col("name") == "_PRENOMS_RARES"
is_corsica = pl.col("dpt")=="20"
is_dom_tom = pl.col("dpt").str.starts_with("97")
is_male = pl.col("sexe")=="M"
is_female = pl.col("sexe")=="F"

In [16]:
# import geometric data
url_geojson = "https://france-geojson.gregoiredavid.fr/repo/departements.geojson"
geodata = alt.Data(url=url_geojson, format=alt.DataFormat(property="features"))
centers = pl.read_csv("data/dpt_positions.csv")

In [17]:
babies = (
    babies
        # remove rare nouns
        .filter(~is_rare)
        .filter(pl.col("count").sum().over("name") >= 100)
        
        # remove empty cells in the data
        .drop_nulls()
        
        .filter(pl.col("count").sum().over("name") >= 100)

        .with_columns(
            pl.col("year").floordiv(10).mul(10).alias("decade"),
            pl.col("year").floordiv(3).mul(3).alias("year3"),
        )
)
babies

shape: (3_611_256, 7)
┌──────┬─────┬──────┬───────┬───────┬────────┬───────┐
│ sexe ┆ dpt ┆ year ┆ name  ┆ count ┆ decade ┆ year3 │
│ ---  ┆ --- ┆ ---  ┆ ---   ┆ ---   ┆ ---    ┆ ---   │
│ str  ┆ str ┆ i64  ┆ str   ┆ i64   ┆ i64    ┆ i64   │
╞══════╪═════╪══════╪═══════╪═══════╪════════╪═══════╡
│ M    ┆ 75  ┆ 1962 ┆ AARON ┆ 3     ┆ 1960   ┆ 1962  │
│ M    ┆ 75  ┆ 1976 ┆ AARON ┆ 3     ┆ 1970   ┆ 1974  │
│ M    ┆ 75  ┆ 1982 ┆ AARON ┆ 3     ┆ 1980   ┆ 1980  │
│ M    ┆ 75  ┆ 1984 ┆ AARON ┆ 3     ┆ 1980   ┆ 1983  │
│ M    ┆ 75  ┆ 1985 ┆ AARON ┆ 5     ┆ 1980   ┆ 1983  │
│ …    ┆ …   ┆ …    ┆ …     ┆ …     ┆ …      ┆ …     │
│ F    ┆ 59  ┆ 1928 ┆ ZULMA ┆ 9     ┆ 1920   ┆ 1926  │
│ F    ┆ 62  ┆ 1928 ┆ ZULMA ┆ 3     ┆ 1920   ┆ 1926  │
│ F    ┆ 62  ┆ 1930 ┆ ZULMA ┆ 4     ┆ 1930   ┆ 1929  │
│ F    ┆ 59  ┆ 1931 ┆ ZULMA ┆ 5     ┆ 1930   ┆ 1929  │
│ F    ┆ 62  ┆ 1933 ┆ ZULMA ┆ 5     ┆ 1930   ┆ 1932  │
└──────┴─────┴──────┴───────┴───────┴────────┴───────┘

# Main visualisation

In [18]:
n_names = 20
relative = False

if not relative:
    name_dpt_yr = (
        babies
            .group_by(["name", "dpt", "year3"]).agg(pl.col("count").sum())
            .with_columns((pl.col("count") / pl.col("count").sum().over(["year3"])).alias("count_percent"))
            .filter(pl.sum("count").over("name").rank("dense", descending=True) <= n_names)
    )

else:
    name_dpt_yr = (
        babies
            .filter(pl.sum("count").over("name").rank("dense", descending=True) <= n_names)
            .group_by(["name", "dpt", "year3"]).agg(pl.col("count").sum())
            .with_columns((pl.col("count") / pl.col("count").sum().over(["year3"])).alias("count_percent"))
    )

if not relative:
    accu = (
        name_dpt_yr.group_by(["year3","name"])
        .agg(pl.col("count_percent").sum())
    )
else:
    accu = (
        name_dpt_yr_pre.group_by(["year3","name"])
        .agg(pl.col("count_percent").sum())
    )
    


In [19]:
custom_colors = [
    '#e6194b', '#3cb44b', '#ffe119', '#4363d8', '#f58231',
    '#911eb4', '#46f0f0', '#f032e6', '#bcf60c', '#fabebe',
    '#008080', '#e6beff', '#9a6324', '#fffac8', '#800000',
    '#aaffc3', '#808000', '#ffd8b1', '#000075', '#808080',
    '#ffffff', '#000000', '#a9a9a9', '#00ff00', '#ff00ff'
]

aggre = alt.Chart(accu, width=800, height=400, title = "Évolution des prénoms par date").mark_bar(width=15).encode(
    x=alt.X('year3:Q').title("Année (aggrégée)"),
    y=alt.Y('count_percent:Q').title("Proportion des Naissances"),
    color = alt.Color('name'
                    #   ,scale=alt.Scale(scheme=alt.SequentialMultiHue())
                    ,scale=alt.Scale(range=custom_colors)).legend(columns=2),
    tooltip = [alt.Tooltip('year3',title="Année"),alt.Tooltip('name', title='Nom'), alt.Tooltip('count_percent:Q', title='Naissances')],
)
aggre

alt.Chart(...)

In [20]:
click_dpt = alt.selection_point(fields=['dpt'])
pop_selection = alt.selection_interval(encodings=['x'])
selection = alt.selection_point(fields=['name'])

color = alt.condition(selection, alt.Color('name:N', legend=None), alt.value('lightgray'))

make = pl.DataFrame({'name': name_dpt_yr.select("name").unique().to_series().to_list()})
make_selector = alt.Chart(make).mark_rect().encode(y=alt.Y('name',title="Noms (à sélectionner)") , color=color).add_params(selection).add_params(pop_selection)

In [21]:
population = alt.Chart(name_dpt_yr, width=800, height=300, title = "Évolution des prénoms par date").mark_bar(width=15).encode(
    x=alt.X('year3').title("Année (aggrégée)"),
    y=alt.Y('count_percent:Q').title("Proportion des Naissances"),
    color = alt.Color('name'
                    #   ,scale=alt.Scale(scheme=alt.SequentialMultiHue())
                    ,scale=alt.Scale(range=custom_colors)).legend(columns=2),
    tooltip = [alt.Tooltip('year3',title="Année"),alt.Tooltip('dpt',title='Département'),alt.Tooltip('name', title='Nom'), alt.Tooltip('count:Q', title='Naissances')],
).add_params(pop_selection
).add_params(selection
).transform_filter(click_dpt
).transform_filter(selection
)

alt.data_transformers.disable_max_rows()
map = (alt.Chart(name_dpt_yr, width=800)
.mark_geoshape()
.transform_lookup(
    lookup='dpt',
    from_=alt.LookupData(geodata, 'properties.code'),
      as_="geo"
)
.transform_filter(selection)
.encode(
    color=alt.Color('sum(count):Q').title("Naissances locales"), 
    shape='geo:G',
    tooltip = [alt.Tooltip('dpt:N', title='Département'), alt.Tooltip('sum(count):Q', title='Naissances')],
    stroke = alt.condition(
        click_dpt,  # Highlight the selected department
        alt.value('black'),  # Stroke color for the selected department
        alt.value('transparent')
    ))
.add_params(click_dpt)
.transform_filter(pop_selection)
)

In [22]:
make_selector | (population & map) 

alt.HConcatChart(...)

# Diversity and big names

In [23]:
diversity = (
    babies
    .filter(pl.col("decade") != 2020, ~is_corsica, ~is_dom_tom)
    .group_by("dpt", "sexe", "decade", "name")
    .agg(pl.col("count").sum().alias("births"))
    .with_columns([
        # Calculate total births per (department, sex, decade, noun) if needed
        pl.col("births").sum().over("sexe", "decade").alias("total_births_decade"),
        pl.col("births").sum().over("sexe", "decade", "dpt").alias("total_births_dpt"),
        pl.col("births").sum().over("sexe", "decade", "name").alias("births_decade"),
        pl.col("births").rank(method="dense", descending=True).over(["sexe", "decade", "dpt"]).alias("rank_dpt"),
    ])
    .with_columns([
        # Mark if name is in top 50
        (pl.col("rank_dpt") <= 5).alias("is_top5"),
    ])
    .group_by(["dpt", "sexe", "decade"])
    .agg([
        pl.col("total_births_dpt").first(),
        # Sum births for top 50 names
        pl.col("births").filter(pl.col("is_top5")).sum().alias("top5_births"),
        # Get total births (same for all rows in group, so first() works)
        pl.col("total_births_decade").first().alias("total_births"),
        pl.col("name").filter(pl.col("is_top5")).unique().head().str.join(", ").alias("top_noun"),
    ])
    .with_columns([
        # Calculate proportion
        (pl.col("top5_births") / pl.col("total_births_dpt")).alias("top5_score"),
    ])
)

In [24]:
data = (alt.Chart(diversity, title="Proportion des prénoms dans le top5 de leur département")
    .transform_lookup(
        lookup='dpt',
        from_=alt.LookupData(geodata, 'properties.code'),
        as_="geo"
    )
    .transform_lookup(
        lookup='dpt',
        from_=alt.LookupData(centers, 'dpt', ["lon", "lat"]),
    )
)


fg = data.mark_circle().encode(
    alt.Latitude("lat:Q"),
    alt.Longitude("lon:Q"),
    alt.Size("top5_score:Q"),
    alt.Order("sexe"),
    alt.Column("decade"),
    alt.Row("sexe"),
    alt.Fill("sexe"),
    alt.Color("top5_score:Q"),
    alt.OpacityValue(0.5),
    tooltip=[alt.Tooltip("dpt"), 
             alt.Tooltip("top_noun"), 
             alt.Tooltip("top5_score").format("0.0%"),
             alt.Tooltip("total_births_dpt")
            ],
)

fg

alt.Chart(...)

# Baptemes

In [25]:
baptems_yr = pl.read_csv("data/baptemes.csv")

In [26]:
noms_cathos = ["MARIE", "CHRISTIAN", "CATHERINE", "JOSEPH", "PIERRE", "PAUL","DOMINIQUE","MICHEL","JACQUES","JEAN","JEANNE"]
extras=[]#["ANDRÉ","BERNARD","GEORGES"]
noms_cathos +=extras

cathos_yr = (
    # first, remove rare nouns
    df.filter(pl.col("name").is_in(noms_cathos))
    .filter(pl.col("year") >= 2000)
    .group_by(["year"])
    .agg(pl.col("count").sum())
)
cathos_yr
joined = cathos_yr.join(baptems_yr, "year")
joined

shape: (8, 3)
┌──────┬───────┬─────────┐
│ year ┆ count ┆ baptems │
│ ---  ┆ ---   ┆ ---     │
│ i64  ┆ i64   ┆ i64     │
╞══════╪═══════╪═════════╡
│ 2017 ┆ 8275  ┆ 231165  │
│ 2016 ┆ 8668  ┆ 249921  │
│ 2010 ┆ 9679  ┆ 302941  │
│ 2020 ┆ 6710  ┆ 112123  │
│ 2000 ┆ 18533 ┆ 400327  │
│ 2018 ┆ 7856  ┆ 215551  │
│ 2019 ┆ 7514  ┆ 204304  │
│ 2015 ┆ 9136  ┆ 262314  │
└──────┴───────┴─────────┘

In [27]:
base = alt.Chart(joined,width=800, height=200, title = "Évolution des prénoms à consonnance catholique / Nombre de baptèmes").encode(
    alt.X("year:T").title("Année")
)

histogram_maries = base.mark_line(color='#57A44C').encode(
y=alt.Y('count:Q').axis(title="Naissances",titleColor='#57A44C',domainColor='#57A44C',labelColor='#57A44C'),
#color = alt.Color('name'),
#tooltip = [alt.Tooltip('name', title='Name'), alt.Tooltip('count:Q', title='Count')],
)

histogram_baptems = base.mark_line(color="#4C7EA4").encode(
y=alt.Y('baptems:Q').axis(title="Baptèmes",titleColor='#4C7EA4',domainColor='#4C7EA4',labelColor='#4C7EA4'),
#color = alt.Color('name'),
#tooltip = [alt.Tooltip('name', title='Name'), alt.Tooltip('count:Q', title='Count')],
)

alt.layer(histogram_baptems,histogram_maries).resolve_scale(
    y='independent'
)

alt.LayerChart(...)

# Sexe

In [28]:
neutral_names = (babies
    .group_by("name")
    .agg(
        pl.col("count").sum(),
        (pl.col("count").filter(is_male).sum() / pl.col("count").filter(is_female).sum()).log10().alias("sex_score")
    )
    .filter(pl.col("sex_score").is_between(-1, 1))
    .sort("count", descending=True)
    .head(6)
)
neutral_babies = (
    babies
        .join(neutral_names, on="name")
        .group_by("decade", "name", "dpt")
        .agg(
            pl.sum("count").log().alias("lc"),
            pl.sum("count"),
            (pl.col("count").filter(is_male).sum() / pl.col("count").sum()).alias("male_proportion")
        )
)
neutral_babies

shape: (4_379, 6)
┌────────┬───────────┬─────┬──────────┬───────┬─────────────────┐
│ decade ┆ name      ┆ dpt ┆ lc       ┆ count ┆ male_proportion │
│ ---    ┆ ---       ┆ --- ┆ ---      ┆ ---   ┆ ---             │
│ i64    ┆ str       ┆ str ┆ f64      ┆ i64   ┆ f64             │
╞════════╪═══════════╪═════╪══════════╪═══════╪═════════════════╡
│ 2020   ┆ NOA       ┆ 08  ┆ 1.609438 ┆ 5     ┆ 1.0             │
│ 1960   ┆ DOMINIQUE ┆ 27  ┆ 7.063904 ┆ 1169  ┆ 0.754491        │
│ 1960   ┆ CAMILLE   ┆ 57  ┆ 3.332205 ┆ 28    ┆ 0.892857        │
│ 2020   ┆ ANDRÉA    ┆ 67  ┆ 1.386294 ┆ 4     ┆ 0.0             │
│ 1990   ┆ ANDRÉA    ┆ 31  ┆ 5.105945 ┆ 165   ┆ 0.127273        │
│ …      ┆ …         ┆ …   ┆ …        ┆ …     ┆ …               │
│ 2000   ┆ CLAUDE    ┆ 973 ┆ 3.258097 ┆ 26    ┆ 1.0             │
│ 1900   ┆ ALIX      ┆ 58  ┆ 1.791759 ┆ 6     ┆ 1.0             │
│ 2010   ┆ DOMINIQUE ┆ 93  ┆ 1.098612 ┆ 3     ┆ 1.0             │
│ 1930   ┆ ANDRÉA    ┆ 33  ┆ 4.043051 ┆ 57    ┆ 0.0             │
│ 1970   ┆ DOMINIQUE ┆ 47  ┆ 5.247024 ┆ 190   ┆ 0.668421        │
└────────┴───────────┴─────┴──────────┴───────┴─────────────────┘

In [29]:
time_slider = alt.binding_range(min=1940, max=2010, step=10, name="Decade")
time_value = alt.param(bind=time_slider, value=1950)

data = (
    alt.Chart(neutral_babies, title="Evolution of neutral names")
    .add_params(time_value)
    .transform_filter(alt.datum.decade==time_value)
    .transform_lookup(
        lookup='dpt',
        from_=alt.LookupData(geodata, 'properties.code'),
        as_="geo"
    )
    .transform_lookup(
        lookup='dpt',
        from_=alt.LookupData(centers, 'dpt', ["lon", "lat"]),
    )
)
chart = (data
    .mark_geoshape()
    .encode(
        alt.Shape("geo:G"),
        alt.Color("male_proportion:Q"),
        alt.Tooltip(["male_proportion", "count"]),
        opacity="lc"
    )
)

chart.facet("name", columns=3)


alt.FacetChart(...)

In [30]:
# Load and filter the dataset
df = pl.read_csv("data/dataset.csv")

# Filter from 1970 to 2030 and exclude "_PRENOMS_RARES"
filtered_df = (
    df
    .filter(
        (pl.col("year") >= 1970) & 
        (pl.col("year") <= 2030) & 
        (pl.col("name") != "_PRENOMS_RARES")
    )
)

# Group by name and sum the counts
top_names_df = (
    filtered_df
    .group_by("name")
    .agg(pl.col("count").sum().alias("total_count"))
    .sort("total_count", descending=True)
    .head(20)
)

# Extract just the names as a Python list
top_names_70 = top_names_df["name"].to_list()

print(top_names_70)

# Total number of all births (for selected names, for example)
total_births = df.filter(pl.col("name").is_in(top_names_70))["count"].sum()

# Add a new column with global proportion
accu = (
    df
    .filter(pl.col("name").is_in(top_names_70))
    .group_by(["year", "name"])
    .agg(pl.col("count").sum())
    .with_columns(
        (pl.col("count") / total_births).alias("count_percent")
    )
    .sort("year")
)
accu

aggre = alt.Chart(accu, width=900, height=400, title = "Évolution des prénoms par date").mark_bar().encode(
    x=alt.X('year:Q').title("Année (aggrégée)"),
    y=alt.Y('count_percent:Q').title("Proportion des Naissances"),
    color = alt.Color('name'
                    #   ,scale=alt.Scale(scheme=alt.SequentialMultiHue())
                    ,scale=alt.Scale(range=custom_colors)).legend(columns=2),
    tooltip = [alt.Tooltip('year',title="Année"),alt.Tooltip('name', title='Nom'), alt.Tooltip('count_percent:Q', title='Naissances')],
)

aggre


['NICOLAS', 'SÉBASTIEN', 'JULIEN', 'DAVID', 'THOMAS', 'ALEXANDRE', 'MARIE', 'CHRISTOPHE', 'STÉPHANIE', 'STÉPHANE', 'CÉLINE', 'CAMILLE', 'GUILLAUME', 'MAXIME', 'FRÉDÉRIC', 'JULIE', 'SANDRINE', 'ROMAIN', 'VINCENT', 'AURÉLIE']


alt.Chart(...)